In [1]:
import math
import numpy as np

In [2]:
def getfocus(a,ecc):
    c=a*ecc
    return c

In [3]:
def getsemiminor(a,ecc):
    c=getfocus(a,ecc)
    b=np.sqrt(a**2-c**2)
    return b

In [4]:
import math
def InitialDataEqualMassConic(radius,ecc,angle,initmass):
    orbitalangle=angle
    print("angle",angle)
    phi=np.array([math.pi+orbitalangle,orbitalangle])
    orbitalradius=radius #semimajor axis
    eccentricity=ecc
    print(eccentricity)
    mass=np.ones(2)
    masses=initmass*mass #*masssun (natural units)
    return phi,orbitalangle,orbitalradius,eccentricity, masses
    

In [5]:
import random,numpy as np
rad0=50.
ecc0=0.5
theta0=math.pi/6. #math.pi/6.
mass0=1.0
initdateqellipse=InitialDataEqualMassConic(rad0,ecc0,theta0,mass0)
print(initdateqellipse)

angle 0.5235987755982988
0.5
(array([3.66519143, 0.52359878]), 0.5235987755982988, 50.0, 0.5, array([1., 1.]))


In [60]:
def getxyuveqtwoellipses(initdat):
    phi,orbitangle,orbitalradius,eccentricity, masses=initdat
    print("initdat", orbitalradius, phi, eccentricity, np.cos(phi), np.sin(phi))
    metersperAU=1
    Gconstant=1
    #fix x0 y0 at one star, disregard initial data, use orbital radius as separation between stars
    #this is consistant with choice in previous part
    cosphi=np.cos(phi)
    sinphi=np.sin(phi)
    coordsep=orbitalradius #/2.
    print("coordsep",coordsep)
    #x0=orbitalradius/2.*np.cos(phi)*metersperAU
    #y0=orbitalradius/2.*np.sin(phi)*metersperAU
    count=0
    for phi0 in phi:
        if phi0==0:
            print("zero")
            #x0[count]=orbitalradius[count]/2.
            #y0[count]=0
            cosphi[count]=1.0
            sinphi[count]=0.0
        if phi0==math.pi:
            cosphi[count]=-1.0
            sinphi[count]=0.0
            print("pi")
            #x0[count]=-orbitalradius[count]/2.
            #y0[count]=0
        if phi0==math.pi/2.:
            cosphi[count]=0.0
            sinphi[count]=1.0
            #x0[count]=0
            #y0[count]=orbitalradius[count]/2.
        if phi0==3*math.pi/2.:
            cosphi[count]=0.0
            sinphi[count]=-1.0
            #x0[count]=0
            #y0[count]=-orbitalradius[count]/2.
        count+=1
    x0=coordsep*cosphi
    y0=coordsep*sinphi
    #x0[1]=0.0
    #y0[1]=0.0
    z0=np.zeros(2)
    print(x0)
    print(y0)
    v=np.zeros(2)
    a=np.zeros(2)
    ux0=0.
    uy0=0.
    uz0=0.
    ax0=0.
    ay0=0.
    az0=0.
    vx0=0.
    vy0=0.
    vz0=0.
    print(eccentricity)
    #masses=np.zeros(2)
    #masses[0]=masses[1]+masses[0]
    #masses[1]=(masses[1]*masses[0])/(masses[1]+masses[0])
    if eccentricity<1 and eccentricity>0:
        #elliptical
        orbitalr=orbitalradius #NO REDUCED MASS 
        #focusdisp=getfocus(orbitalr,eccentricity) #displacement of the center due to the focus being at the center
        coordsep=orbitalr*(1+eccentricity) #start at aphelion
        x0=(coordsep)*cosphi
        y0=(coordsep)*sinphi
        starsep=np.sqrt((x0[0]-x0[1])**2+(y0[0]-y0[1])**2) #two stars, at opposite ends of the orbit
        Fapastron=masses[1]*masses[0]/starsep**2
        #print('xycomp',coordsep,focusdisp,x0,y0)
        #x0[0]=0.0
        #y0[0]=0.0
        v=np.zeros(2)
        #v= np.sqrt(masses[1]*masses[0]/masses*(2./starsep-1./(2*orbitalr)))
        #vsq=masses[1]*masses[0]/masses/orbitalr*(1-eccentricity)/(1+eccentricity)
        vapsq=masses[1]*masses[0]/masses*(1./(coordsep)-1./orbitalr)/2.
        v=np.sqrt(vapsq)
        #v= np.sqrt(masses[1]*masses[0]/masses*(1./orbitalr-2./starsep))
        ux0=-v*sinphi
        uy0=v*cosphi #initial data in y only 
        uz0=np.zeros(2)
    
        print("vstuff", coordsep,orbitalr, 2./coordsep, 1./orbitalr, (2./starsep-1./(2.*orbitalr)), 1./(coordsep))
        
        a=np.zeros(2)
        a=Fapastron/masses
    
        ax0=-a*cosphi
        ay0=-a*sinphi
        az0=np.zeros(2)
    elif eccentricity[0]==0.0: #circular
        #start at perihelion for both (eliptical, doesn't generalize to three body)
        #actually start with circular orbit
        ux0=np.zeros(2) #*149597870700
        #centrepital force balances gravitational force
        metersperAU=1 #natural units
        #G=1
        Gconstant=1
        #Fcentripital=mass1*v**2/rphys
        #centF=accel
        #Faccel=G*m1*m2/r^2
        r0=2.*orbitalradius #Mystery factor of 2
        print("r0", r0)
        v=np.zeros(2)
        for i in np.arange(2):
            v[i]=np.sqrt(Gconstant*masses[(i+1)%2]/np.abs(r0[i]))
        print(v)
        #r0=orbitalradius #np.sqrt(x0**2+y0**2)
        ux0=-v[0]*sinphi
        uy0=v[1]*cosphi #initial data in y only 
        uz0=np.zeros(2)
    
        a=np.zeros(2)
        a=Fapastron/masses
    
        ax0=-a[0]*cosphi
        ay0=-a[1]*sinphi
        az0=np.zeros(2)

    statevec=[]
    avec=[]
    for i in np.arange(len(x0)):
        stateveci=np.array([x0[i],y0[i],z0[i],ux0[i],uy0[i],uz0[i]])
        aveci=np.array([ax0[i],ay0[i],az0[i]])
        statevec.append(stateveci)
        avec.append(aveci)
    statevecnp=np.array(statevec)
    avecnp=np.array(avec)
    return masses, statevecnp,avecnp

In [61]:
xyuvaeqellipse=getxyuveqtwoellipses(initdateqellipse)
print(xyuvaeqellipse)
masses,xvec,avec=xyuvaeqellipse

initdat 50.0 [3.66519143 0.52359878] 0.5 [-0.8660254  0.8660254] [-0.5  0.5]
coordsep 50.0
[-43.30127019  43.30127019]
[-25.  25.]
0.5
vstuff 75.0 50.0 0.02666666666666667 0.02 0.003333333333333334 0.013333333333333334
(array([1., 1.]), array([[-64.95190528, -37.5       ,   0.        ,          nan,
                 nan,   0.        ],
       [ 64.95190528,  37.5       ,   0.        ,          nan,
                 nan,   0.        ]]), array([[ 3.84900179e-05,  2.22222222e-05,  0.00000000e+00],
       [-3.84900179e-05, -2.22222222e-05,  0.00000000e+00]]))


/Users/sdorsher/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:77: RuntimeWarning: invalid value encountered in sqrt


In [51]:
def RK4implicit(h,t,xvec,f): #not a finite difference so no step in y
    k1= h*f(t,xvec)
    k2=h*f(t+h/2, xvec+k1/2)
    k3=h*f(t+h/2,xvec+k2/2)
    k4=h*f(t+h,xvec+k3)
    return t+h, xvec+1/6.*(k1+2.*k2+2.*k3+k4)

In [52]:
class OrbitDiffEqOld:
    def __init__(self,masses,xvec,avec,t0):
        self.masses=masses
        self.xvec=xvec
        self.ti=t0
        self.avec=avec
    def dxidt(self,t,xvec):
        return xvec[:,3].transpose()
    def dyidt(self,t,xvec):
        return xvec[:,4].transpose()
    def dzidt(self,t,xvec):
        return xvec[:,5].transpose()
    def dvxidt(self,t,xvec):
        #return axi[m]
        axii=np.zeros(len(xvec[:,0]))
        rii=np.sqrt(xvec[:,0]**2+xvec[:,1]**2+xvec[:,2]**2)
        Gconstant=1 #6.408*10**-11
        for k in np.arange(len(rii)):
            for j in np.arange(len(rii)):
                if j!=k:
                    #print(j,k,xvec[j,0],xvec[k,0],xvec[j,0]-xvec[k,0])
                    rreljk=np.abs((xvec[j,0] - xvec[k,0])**2+(xvec[j,1]-xvec[k,1])**2+(xvec[j,2]-xvec[k,2])**2)**(1./2.)
                    axii[j]-=Gconstant*self.masses[k]*(xvec[j,0]  - xvec[k,0])/rreljk**3
        return axii
    def dvyidt(self,t,xvec):
        #return axi[m]
        ayii=np.zeros(len(xvec[:,0]))
        rii=np.sqrt(xvec[:,0]**2+xvec[:,1]**2+xvec[:,2]**2)
        Gconstant=1 #6.408*10**-11
        for k in np.arange(len(rii)):
            for j in np.arange(len(rii)):
                if j!=k:
                    rreljk=np.abs((xvec[j,0] - xvec[k,0])**2+(xvec[j,1]-xvec[k,1])**2+(xvec[j,2]-xvec[k,2])**2)**(1./2.)
                    ayii[j]-=Gconstant*self.masses[k]*(xvec[j,1]  - xvec[k,1])/rreljk**3
        return ayii
    def dvzidt(self,t,xvec):
        #return axi[m]
        azii=np.zeros(len(xvec[:,0]))
        rii=np.sqrt(xvec[:,0]**2+xvec[:,1]**2+xvec[:,2]**2)
        Gconstant=1 #6.408*10**-11
        for k in np.arange(len(rii)):
            for j in np.arange(len(rii)):
                if j!=k:
                    rreljk=np.abs((xvec[j,0] - xvec[k,0])**2+(xvec[j,1]-xvec[k,1])**2+(xvec[j,2]-xvec[k,2])**2)**(1./2.)
                    azii[j]-=Gconstant*self.masses[k]*(xvec[j,2]  - xvec[k,2])/rreljk**3
        return azii
    
    def dvecdt(self,t,xvec):
        avec=np.array([self.dvxidt(self,xvec),self.dvyidt(self,xvec),self.dvzidt(self,xvec)])
        print("avec", avec)
        avecT=avec.transpose()
        self.avec=avecT
        dvec2=np.array([self.dxidt(t,xvec),self.dyidt(t,xvec),self.dzidt(self,xvec),avec[0,:],avec[1,:],avec[2,:]])
                       
        dvec2T=dvec2.transpose()
        return dvec2T
    def updateINTERNAL(self,xvecii,tii):
        self.xvec=xvecii
        self.ti=tii
        return self
    def update(self,xvecii,avecii,tii):
        self.xvec=xvecii
        self.avec=avecii,
        self.ti=tii
    def print2D(self):
        print(self.masses,self.xvec,self.ti)
        return self
    def list2D(self):
        return self.masses,self.xvec,self.avec,self.ti
    def timestepRK4ODE(self,step,dt):

    
        h=dt
        #tnew,ynew, intval=RK4(h,t,y,f)
        #m represents choices of mass
        i=step
        
        tnew,intvalxvec=RK4implicit(h,self.ti,self.xvec,self.dvecdt)
        #xii = intvalx
        #tnew,intvalvx=RK4implicit(h,self.ti,self.vxi,self.dvxidt)
        #vxii=intvalvx
        #tnew,intvaly=RK4implicit(h,self.ti,self.yi,self.dyidt)
        #yii = intvaly
        #tnew,intvalvy=RK4implicit(h,self.ti,self.vyi,self.dvyidt)
        #vyii=intvalvy
        #tnew,intvalz=RK4implicit(h,self.ti,self.zi,self.dzidt)
        #zii = intvalz
        #tnew,intvalvz=RK4implicit(h,self.ti,self.vzi,self.dvzidt)
        #vzii=intvalvz
        #axii=self.dvxidt(self.ti,np.zeros(np.shape(self.xi)))
        #ayii=self.dvyidt(self.ti,np.zeros(np.shape(self.yi)))
        #azii=self.dvzidt(self.ti,np.zeros(np.shape(self.zi)))
 
        #print(xii)
        self.updateINTERNAL(intvalxvec,tnew)
        return self.masses, self.xvec,self.avec,self.ti

In [53]:
class OrbitDiffEq:
    def __init__(self,masses,xvec,avec,t0):
        self.masses=masses
        self.xvec=xvec
        self.ti=t0
        self.avec=avec
    def dxidt(self,t,xvec):
        return xvec[:,3].transpose()
    def dyidt(self,t,xvec):
        return xvec[:,4].transpose()
    def dzidt(self,t,xvec):
        return xvec[:,5].transpose()
    def dvxidt(self,t,xvec):
        #return axi[m]
        axii=np.zeros(len(xvec[:,0]))
        #rii=np.sqrt(np.sum(xvec[:,0:3])**2)
        Gconstant=1 #6.408*10**-11
        for k in np.arange(len(xvec[:,0])):
            for j in np.arange(len(xvec[:,0])):
                if j!=k:
                    vecshift=xvec[j,:]-xvec[k,:]
                    #print(j,k,xvec[j,0],xvec[k,0],xvec[j,0]-xvec[k,0])
                    rreljk=np.sqrt(np.sum(vecshift[0:3]**2))
                    axii[j]-=Gconstant*self.masses[k]*(vecshift[0])/rreljk**3
        return axii
    def dvyidt(self,t,xvec):
        #return axi[m]
        ayii=np.zeros(len(xvec[:,0]))
        #rii=np.sqrt(np.sum(xvec[:,0:3]**2))
        Gconstant=1 #6.408*10**-11
        for k in np.arange(len(xvec[:,1])):
            for j in np.arange(len(xvec[:,1])):
                if j!=k:
                    vecshift=xvec[j,:]-xvec[k,:]
                    rreljk=np.sqrt(np.sum(vecshift[0:3]**2))
                    ayii[j]-=Gconstant*self.masses[k]*(vecshift[1])/rreljk**3
        return ayii
    def dvzidt(self,t,xvec):
        #return axi[m]
        azii=np.zeros(len(xvec[:,0]))
        #rii=np.sqrt(np.squm(xvec[:,0:3]**2))
        Gconstant=1 #6.408*10**-11
        for k in np.arange(len(xvec[:,1])):
            for j in np.arange(len(xvec[:,1])):
                if j!=k:
                    vecshift=xvec[j,:]-xvec[k,:]
                    rreljk=np.sqrt(np.sum(vecshift[0:3]**2))
                    azii[j]-=Gconstant*self.masses[k]*(vecshift[2])/rreljk**3
        return azii
    
    def dvecdt(self,t,xvec):
        avec=np.array([self.dvxidt(self,xvec),self.dvyidt(self,xvec),self.dvzidt(self,xvec)])
        print("avec", avec)
        avecT=avec.transpose()
        self.avec=avecT
        dvec2=np.array([self.dxidt(t,xvec),self.dyidt(t,xvec),self.dzidt(self,xvec),avec[0,:],avec[1,:],avec[2,:]])
                       
        dvec2T=dvec2.transpose()
        return dvec2T
    def updateINTERNAL(self,xvecii,tii):
        self.xvec=xvecii
        self.ti=tii
        return self
    def update(self,xvecii,avecii,tii):
        self.xvec=xvecii
        self.avec=avecii,
        self.ti=tii
    def print2D(self):
        print(self.masses,self.xvec,self.ti)
        return self
    def list2D(self):
        return self.masses,self.xvec,self.avec,self.ti
    def timestepRK4ODE(self,step,dt):

    
        h=dt
        #tnew,ynew, intval=RK4(h,t,y,f)
        #m represents choices of mass
        i=step
        
        tnew,intvalxvec=RK4implicit(h,self.ti,self.xvec,self.dvecdt)
        #xii = intvalx
        #tnew,intvalvx=RK4implicit(h,self.ti,self.vxi,self.dvxidt)
        #vxii=intvalvx
        #tnew,intvaly=RK4implicit(h,self.ti,self.yi,self.dyidt)
        #yii = intvaly
        #tnew,intvalvy=RK4implicit(h,self.ti,self.vyi,self.dvyidt)
        #vyii=intvalvy
        #tnew,intvalz=RK4implicit(h,self.ti,self.zi,self.dzidt)
        #zii = intvalz
        #tnew,intvalvz=RK4implicit(h,self.ti,self.vzi,self.dvzidt)
        #vzii=intvalvz
        #axii=self.dvxidt(self.ti,np.zeros(np.shape(self.xi)))
        #ayii=self.dvyidt(self.ti,np.zeros(np.shape(self.yi)))
        #azii=self.dvzidt(self.ti,np.zeros(np.shape(self.zi)))
 
        #print(xii)
        self.updateINTERNAL(intvalxvec,tnew)
        return self.masses, self.xvec,self.avec,self.ti

In [54]:
masses, xvec,avec=xyuvaeqellipse
ODEeq= OrbitDiffEq(masses,xvec,avec,0.0)
ODEeq.print2D()
ODEeq.print2D()

[1. 1.] [[-6.49519053e+01 -3.75000000e+01  0.00000000e+00  4.08248290e-02
  -7.07106781e-02  0.00000000e+00]
 [ 6.49519053e+01  3.75000000e+01  0.00000000e+00 -4.08248290e-02
   7.07106781e-02  0.00000000e+00]] 0.0
[1. 1.] [[-6.49519053e+01 -3.75000000e+01  0.00000000e+00  4.08248290e-02
  -7.07106781e-02  0.00000000e+00]
 [ 6.49519053e+01  3.75000000e+01  0.00000000e+00 -4.08248290e-02
   7.07106781e-02  0.00000000e+00]] 0.0


In [55]:
dt=1 #natural units #*31556926 #seconds per year
numsteps=6000
masses,xvec0,avec0=xyuvaeqellipse
ODEeq= OrbitDiffEq(masses,xvec0,avec0,0.0)
ODEeq.print2D()
t=0.0
star1x=[]
star2x=[]
star1a=[]
star2a=[]
times=[]
for i in np.arange(1,numsteps):
    masses,xvec,avec,t=ODEeq.timestepRK4ODE(i,dt)
    ODEeq.print2D()
    star1x.append(xvec[0])
    star2x.append(xvec[1])
    star1a.append(avec[0])
    star2a.append(avec[1])
    times.append(t)



[1. 1.] [[-6.49519053e+01 -3.75000000e+01  0.00000000e+00  4.08248290e-02
  -7.07106781e-02  0.00000000e+00]
 [ 6.49519053e+01  3.75000000e+01  0.00000000e+00 -4.08248290e-02
   7.07106781e-02  0.00000000e+00]] 0.0
avec [[ 3.84900179e-05 -3.84900179e-05]
 [ 2.22222222e-05 -2.22222222e-05]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[ 3.84779046e-05 -3.84779046e-05]
 [ 2.22431636e-05 -2.22431636e-05]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[ 3.84779160e-05 -3.84779160e-05]
 [ 2.22431702e-05 -2.22431702e-05]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[ 3.84657799e-05 -3.84657799e-05]
 [ 2.22640985e-05 -2.22640985e-05]
 [ 0.00000000e+00  0.00000000e+00]]
[1. 1.] [[-6.49110612e+01 -3.75706996e+01  0.00000000e+00  4.08633070e-02
  -7.06884350e-02  0.00000000e+00]
 [ 6.49110612e+01  3.75706996e+01  0.00000000e+00 -4.08633070e-02
   7.06884350e-02  0.00000000e+00]] 1.0
avec [[ 3.84657799e-05 -3.84657799e-05]
 [ 2.22640985e-05 -2.22640985e-05]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[ 3.84536

   6.85737550e-02  0.00000000e+00]] 89.0
avec [[ 3.59947401e-05 -3.59947401e-05]
 [ 2.57153712e-05 -2.57153712e-05]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[ 3.59789051e-05 -3.59789051e-05]
 [ 2.57335111e-05 -2.57335111e-05]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[ 3.59789157e-05 -3.59789157e-05]
 [ 2.57335187e-05 -2.57335187e-05]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[ 3.59630619e-05 -3.59630619e-05]
 [ 2.57516405e-05 -2.57516405e-05]
 [ 0.00000000e+00  0.00000000e+00]]
[1. 1.] [[-6.11249672e+01 -4.37690256e+01  0.00000000e+00  4.41803025e-02
  -6.85480215e-02  0.00000000e+00]
 [ 6.11249672e+01  4.37690256e+01  0.00000000e+00 -4.41803025e-02
   6.85480215e-02  0.00000000e+00]] 90.0
avec [[ 3.59630619e-05 -3.59630619e-05]
 [ 2.57516405e-05 -2.57516405e-05]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[ 3.59471894e-05 -3.59471894e-05]
 [ 2.57697442e-05 -2.57697442e-05]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[ 3.59472000e-05 -3.59472000e-05]
 [ 2.57697518e-05 -2.57697518e-05]
 [

avec [[ 3.37357305e-05 -3.37357305e-05]
 [ 2.79617506e-05 -2.79617506e-05]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[ 3.37176549e-05 -3.37176549e-05]
 [ 2.79773062e-05 -2.79773062e-05]
 [ 0.00000000e+00  0.00000000e+00]]
[1. 1.] [[-5.81323162e+01 -4.82354309e+01  0.00000000e+00  4.64813789e-02
  -6.67731009e-02  0.00000000e+00]
 [ 5.81323162e+01  4.82354309e+01  0.00000000e+00 -4.64813789e-02
   6.67731009e-02  0.00000000e+00]] 156.0
avec [[ 3.37176549e-05 -3.37176549e-05]
 [ 2.79773062e-05 -2.79773062e-05]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[ 3.36995645e-05 -3.36995645e-05]
 [ 2.79928413e-05 -2.79928413e-05]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[ 3.36995743e-05 -3.36995743e-05]
 [ 2.79928494e-05 -2.79928494e-05]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[ 3.36814691e-05 -3.36814691e-05]
 [ 2.80083638e-05 -2.80083638e-05]
 [ 0.00000000e+00  0.00000000e+00]]
[1. 1.] [[-5.80858180e+01 -4.83021900e+01  0.00000000e+00  4.65150785e-02
  -6.67451081e-02  0.00000000e+00]
 [ 5.808

 [ 0.00000000e+00  0.00000000e+00]]
[1. 1.] [[-5.49442439e+01 -5.26449453e+01  0.00000000e+00  4.86565485e-02
  -6.48330520e-02  0.00000000e+00]
 [ 5.49442439e+01  5.26449453e+01  0.00000000e+00 -4.86565485e-02
   6.48330520e-02  0.00000000e+00]] 223.0
avec [[ 3.11748117e-05 -3.11748117e-05]
 [ 2.98702128e-05 -2.98702128e-05]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[ 3.11550244e-05 -3.11550244e-05]
 [ 2.98828662e-05 -2.98828662e-05]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[ 3.11550333e-05 -3.11550333e-05]
 [ 2.98828747e-05 -2.98828747e-05]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[ 3.11352355e-05 -3.11352355e-05]
 [ 2.98955060e-05 -2.98955060e-05]
 [ 0.00000000e+00  0.00000000e+00]]
[1. 1.] [[-5.48955718e+01 -5.27097634e+01  0.00000000e+00  4.86877035e-02
  -6.48031692e-02  0.00000000e+00]
 [ 5.48955718e+01  5.27097634e+01  0.00000000e+00 -4.86877035e-02
   6.48031692e-02  0.00000000e+00]] 224.0
avec [[ 3.11352355e-05 -3.11352355e-05]
 [ 2.98955060e-05 -2.98955060e-05]
 [ 0.000000

avec [[ 2.84646202e-05 -2.84646202e-05]
 [ 3.13570205e-05 -3.13570205e-05]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[ 2.84437336e-05 -2.84437336e-05]
 [ 3.13666843e-05 -3.13666843e-05]
 [ 0.00000000e+00  0.00000000e+00]]
[1. 1.] [[-5.16162983e+01 -5.69205209e+01  0.00000000e+00  5.06545987e-02
  -6.27793607e-02  0.00000000e+00]
 [ 5.16162983e+01  5.69205209e+01  0.00000000e+00 -5.06545987e-02
   6.27793607e-02  0.00000000e+00]] 290.0
avec [[ 2.84437336e-05 -2.84437336e-05]
 [ 3.13666843e-05 -3.13666843e-05]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[ 2.84228409e-05 -2.84228409e-05]
 [ 3.13763255e-05 -3.13763255e-05]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[ 2.84228488e-05 -2.84228488e-05]
 [ 3.13763341e-05 -3.13763341e-05]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[ 2.84019501e-05 -2.84019501e-05]
 [ 3.13859526e-05 -3.13859526e-05]
 [ 0.00000000e+00  0.00000000e+00]]
[1. 1.] [[-5.15656295e+01 -5.69832846e+01  0.00000000e+00  5.06830215e-02
  -6.27479844e-02  0.00000000e+00]
 [ 5.156

...

avec [[-2.72925398e-06  2.72925398e-06]
 [ 1.74634995e-06 -1.74634995e-06]
 [ 0.00000000e+00  0.00000000e+00]]
[1. 1.] [[ 2.33973401e+02 -1.49711034e+02  0.00000000e+00  4.24158590e-02
  -9.67621780e-04  0.00000000e+00]
 [-2.33973401e+02  1.49711034e+02  0.00000000e+00 -4.24158590e-02
   9.67621780e-04  0.00000000e+00]] 5743.0
avec [[-2.72925398e-06  2.72925398e-06]
 [ 1.74634995e-06 -1.74634995e-06]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[-2.72896712e-06  2.72896712e-06]
 [ 1.74601378e-06 -1.74601378e-06]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[-2.72896714e-06  2.72896714e-06]
 [ 1.74601379e-06 -1.74601379e-06]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[-2.72868033e-06  2.72868033e-06]
 [ 1.74567771e-06 -1.74567771e-06]
 [ 0.00000000e+00  0.00000000e+00]]
[1. 1.] [[ 2.34015815e+02 -1.49712001e+02  0.00000000e+00  4.24131300e-02
  -9.65875766e-04  0.00000000e+00]
 [-2.34015815e+02  1.49712001e+02  0.00000000e+00 -4.24131300e-02
   9.65875766e-04  0.00000000e+00]] 5744.0
avec [[-2

   8.52107930e-04  0.00000000e+00]] 5810.0
avec [[-2.69121980e-06  2.69121980e-06]
 [ 1.70208494e-06 -1.70208494e-06]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[-2.69093899e-06  2.69093899e-06]
 [ 1.70176042e-06 -1.70176042e-06]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[-2.69093900e-06  2.69093900e-06]
 [ 1.70176043e-06 -1.70176043e-06]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[-2.69065823e-06  2.69065823e-06]
 [ 1.70143600e-06 -1.70143600e-06]
 [ 0.00000000e+00  0.00000000e+00]]
[1. 1.] [[ 2.36851399e+02 -1.49772830e+02  0.00000000e+00  4.22315867e-02
  -8.50406170e-04  0.00000000e+00]
 [-2.36851399e+02  1.49772830e+02  0.00000000e+00 -4.22315867e-02
   8.50406170e-04  0.00000000e+00]] 5811.0
avec [[-2.69065823e-06  2.69065823e-06]
 [ 1.70143600e-06 -1.70143600e-06]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[-2.69037750e-06  2.69037750e-06]
 [ 1.70111166e-06 -1.70111166e-06]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[-2.69037752e-06  2.69037752e-06]
 [ 1.70111167e-06 -1.70111167e-06

 [ 0.00000000e+00  0.00000000e+00]]
avec [[-2.65480994e-06  2.65480994e-06]
 [ 1.66028755e-06 -1.66028755e-06]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[-2.65480996e-06  2.65480996e-06]
 [ 1.66028756e-06 -1.66028756e-06]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[-2.65453490e-06  2.65453490e-06]
 [ 1.65997395e-06 -1.65997395e-06]
 [ 0.00000000e+00  0.00000000e+00]]
[1. 1.] [[ 2.39590794e+02 -1.49824542e+02  0.00000000e+00  4.20578719e-02
  -7.41167958e-04  0.00000000e+00]
 [-2.39590794e+02  1.49824542e+02  0.00000000e+00 -4.20578719e-02
   7.41167958e-04  0.00000000e+00]] 5876.0
avec [[-2.65453490e-06  2.65453490e-06]
 [ 1.65997395e-06 -1.65997395e-06]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[-2.65425989e-06  2.65425989e-06]
 [ 1.65966041e-06 -1.65966041e-06]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[-2.65425991e-06  2.65425991e-06]
 [ 1.65966042e-06 -1.65966042e-06]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[-2.65398494e-06  2.65398494e-06]
 [ 1.65934696e-06 -1.65934696e-06]
 [ 0.

 [ 0.00000000e+00  0.00000000e+00]]
avec [[-2.62238226e-06  2.62238226e-06]
 [ 1.62353145e-06 -1.62353145e-06]
 [ 0.00000000e+00  0.00000000e+00]]
[1. 1.] [[ 2.42067607e+02 -1.49865403e+02  0.00000000e+00  4.19022058e-02
  -6.44310011e-04  0.00000000e+00]
 [-2.42067607e+02  1.49865403e+02  0.00000000e+00 -4.19022058e-02
   6.44310011e-04  0.00000000e+00]] 5935.0
avec [[-2.62238226e-06  2.62238226e-06]
 [ 1.62353145e-06 -1.62353145e-06]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[-2.62211232e-06  2.62211232e-06]
 [ 1.62322733e-06 -1.62322733e-06]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[-2.62211234e-06  2.62211234e-06]
 [ 1.62322734e-06 -1.62322734e-06]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[-2.62184244e-06  2.62184244e-06]
 [ 1.62292330e-06 -1.62292330e-06]
 [ 0.00000000e+00  0.00000000e+00]]
[1. 1.] [[ 2.42109508e+02 -1.49866046e+02  0.00000000e+00  4.18995837e-02
  -6.42686784e-04  0.00000000e+00]
 [-2.42109508e+02  1.49866046e+02  0.00000000e+00 -4.18995837e-02
   6.42686784e-0

avec [[-2.59426999e-06  2.59426999e-06]
 [ 1.59202137e-06 -1.59202137e-06]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[-2.59400447e-06  2.59400447e-06]
 [ 1.59172533e-06 -1.59172533e-06]
 [ 0.00000000e+00  0.00000000e+00]]
[1. 1.] [[ 2.44284754e+02 -1.49897286e+02  0.00000000e+00  4.17639736e-02
  -5.59109523e-04  0.00000000e+00]
 [-2.44284754e+02  1.49897286e+02  0.00000000e+00 -4.17639736e-02
   5.59109523e-04  0.00000000e+00]] 5988.0
avec [[-2.59400447e-06  2.59400447e-06]
 [ 1.59172533e-06 -1.59172533e-06]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[-2.59373899e-06  2.59373899e-06]
 [ 1.59142935e-06 -1.59142935e-06]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[-2.59373901e-06  2.59373901e-06]
 [ 1.59142936e-06 -1.59142936e-06]
 [ 0.00000000e+00  0.00000000e+00]]
avec [[-2.59347357e-06  2.59347357e-06]
 [ 1.59113347e-06 -1.59113347e-06]
 [ 0.00000000e+00  0.00000000e+00]]
[1. 1.] [[ 2.44326516e+02 -1.49897844e+02  0.00000000e+00  4.17613799e-02
  -5.57518093e-04  0.00000000e+00]
 [-2.44

In [56]:
npstar2x=np.array(star2x)
npstar1x=np.array(star1x)
npstar2a=np.array(star2a)
npstar1a=np.array(star1a)
nptimes=np.array(times)

In [57]:
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
output_notebook()
# create a new plot with default tools, using figure
p = figure(title="Elliptical orbit, RK4", plot_width=400, plot_height=400, x_range=(-200,200), y_range=(-200,200))
t = np.linspace(0, 2*math.pi, 100)
focus=getfocus(rad0,ecc0)
b=getsemiminor(rad0,ecc0)
print(ecc0,rad0)
print(b)
print(focus)
#theta0=math.pi/6.
xdim=rad0
ydim=b
# add a circle renderer with x and y coordinates, size, color, and alpha
p.line(npstar1x[:,0],npstar1x[:,1], line_color="purple", legend="Star 1")
p.line(npstar2x[:,0],npstar2x[:,1], line_color="blue", legend="Star 2")
p.line(focus*np.cos(theta0)+xdim*np.cos(t)*np.cos(theta0)-ydim*np.sin(t)*np.sin(theta0),focus*np.sin(theta0)+ydim*np.cos(theta0)*np.sin(t)+xdim*np.sin(theta0)*np.cos(t), line_color="cyan", legend="Ideal ellipse 1")
p.line(-focus*np.cos(theta0)+xdim*np.cos(t)*np.cos(theta0)-ydim*np.sin(t)*np.sin(theta0),-focus*np.sin(theta0)+ydim*np.cos(theta0)*np.sin(t)+xdim*np.sin(theta0)*np.cos(t), line_color="black", legend="Ideal ellipse 2")


print(rad0, b, focus, theta0*180/math.pi)



p.legend.location = "bottom_left"
p.legend.click_policy="hide"

show(p) # show the

Loading BokehJS ...

0.5 50.0
43.30127018922193
25.0
50.0 43.30127018922193 25.0 29.999999999999996


In [39]:
print(theta0)

0.5235987755982988


In [ ]:
print(math.pi/6.0)

In [ ]:
%matplotlib inline
import matplotlib.pyplot as plt
import numpy as np
from matplotlib.patches import Ellipse

NUM = 250

ells = [Ellipse(xy=np.random.rand(2) * 10,
                width=np.random.rand(), height=np.random.rand(),
                angle=np.random.rand() * 360)
        for i in range(NUM)]

fig, ax = plt.subplots(subplot_kw={'aspect': 'equal'})
for e in ells:
    ax.add_artist(e)
    e.set_clip_box(ax.bbox)
    e.set_alpha(np.random.rand())
    e.set_facecolor(np.random.rand(3))

ax.set_xlim(0, 10)
ax.set_ylim(0, 10)

plt.show()

In [ ]:
%matplotlib inline
import matplotlib.pyplot as plt
import numpy as np
from matplotlib.patches import Ellipse

focus=getfocus(rad0,ecc0)
b=getsemiminor(rad0,ecc0)
theta0deg=theta0*180/math.pi
signs=[1,-1]
ells = [Ellipse(xy=[focus*signi*np.cos(theta0),focus*signi*np.sin(theta0)],
                width=2*rad0, height=2*b,
                angle=theta0deg)
                for signi in signs]
                    

fig, ax = plt.subplots(subplot_kw={'aspect': 'equal'})
for e in ells:
    ax.add_artist(e)
    e.set_clip_box(ax.bbox)
    e.set_alpha(0.5)
    e.set_facecolor(np.random.rand(3))

ax.set_xlim(-2*rad0,2*rad0)
ax.set_ylim(-2*rad0, 2*rad0)

print(focus, rad0,b,theta0)
plt.show()